In [1]:
import os
import sys
sys.dont_write_bytecode = True
os.environ["NUMBA_DISABLE_JIT"] = "1"

import pandas as pd
import numpy as np
import plotly.graph_objects as go

from plotly.subplots import make_subplots
from quantfreedom.utils.caching import clear_cache
from quantfreedom.nb.simulate import backtest_df_array_only_nb, simulate_up_to_6_nb
from quantfreedom.indicators.talib_ind import from_talib
from quantfreedom.evaluators.evaluators import eval_is_below, combine_evals, eval_is_above
from quantfreedom.plotting.plot_helper_functions import *
from quantfreedom.enums.enums import (
    LeverageMode,
    SizeType,
    OrderType,
    SL_BE_or_Trail_BasedOn,
)

prices = pd.read_csv(
    "data/30min.csv", index_col="time"
)

In [2]:
rsi_ind = from_talib(
    func_name='rsi',
    df_prices=prices,
    cart_product=False,
    combos=False,
    timeperiod=[15,30,60],
)
rsi_eval = eval_is_below(
    ind_data = rsi_ind,
    user_args=np.arange(30, 51, 10),
)
ema_ind = from_talib(
    func_name='ema',
    df_prices=prices,
    cart_product=False,
    combos=False,
    timeperiod=[200, 400, 600]
)
ema_eval = eval_is_above(
    ind_data=ema_ind,
    df_prices=prices,
    cand_ohlc='close',
)
entries = combine_evals(
    bigger_df=rsi_eval,
    smaller_df=ema_eval,
)
entry = entries.iloc[:, [5]]
final_array, order_records = simulate_up_to_6_nb(
    open_prices=prices.open.values,
    high_prices=prices.high.values,
    low_prices=prices.low.values,
    close_prices=prices.close.values,
    entries=entry.values,
    equity=1000.,
    fee_pct=.06,
    mmr=.5,
    lev_mode=LeverageMode.LeastFreeCashUsed,
    size_type=SizeType.RiskPercentOfAccount,
    order_type=OrderType.LongEntry,
    max_equity_risk_pct=5,
    risk_rewards=10,
    size_pct=1.,
    # sl_pcts=[2,3,4],
    tsl_true_or_false=True,
    tsl_pcts_init=1,
    tsl_based_on=SL_BE_or_Trail_BasedOn.low_price,
    tsl_trail_by_pct=2,
    tsl_when_pct_from_avg_entry=3,
)


In [3]:
def hey_there(
    indicator_dict: dict,
    prices,
):
    amount_of_subplots = 0
    
    for keys in indicator_dict.keys():
        if 'indicator' in keys:
            amount_of_subplots += 1
    
    layout_height = 500 + (250 * amount_of_subplots)
    candle_chart_height_pct = [500 / layout_height]
    
    if amount_of_subplots > 0:
        subchart_heights_pct = np.array([((layout_height - 500) / layout_height) / amount_of_subplots] * amount_of_subplots).tolist()
        row_heights = candle_chart_height_pct + subchart_heights_pct
        fig = make_subplots(
            rows=amount_of_subplots + 1,
            cols=1,
            shared_xaxes=True,
            vertical_spacing=0.02,
            row_heights=row_heights,
        )
    else:
        fig = make_subplots()
    
    open_prices = prices.open.values
    high_prices = prices.high.values
    low_prices = prices.low.values
    close_prices = prices.close.values
    index_prices = prices.index.to_list()
    
    candle_and_ind_list = [
        go.Candlestick(
            x=index_prices,
            open=open_prices,
            high=high_prices,
            low=low_prices,
            close=close_prices,
            name="Candles",
        )
    ]
    if list(indicator_dict.keys())[0] == "candle_chart":
        for candle_ind_key, candle_ind_value in indicator_dict["candle_chart"].items():
            if "values" in candle_ind_key:
                temp_ind_vals = candle_ind_value.values.flatten()
                candle_and_ind_list.append(
                    go.Scatter(
                        x=index_prices,
                        y=temp_ind_vals,
                        mode="lines",
                    )
                )
            elif "entries" in candle_ind_key:
                temp_ind_entries = np.where(
                    candle_ind_value.values.flatten(), temp_ind_vals, np.nan
                ).flatten()
                candle_and_ind_list.append(
                    go.Scatter(
                        x=index_prices,
                        y=temp_ind_entries,
                        mode="markers",
                    )
                )
        del indicator_dict["candle_chart"]
    
    fig.add_traces(data=candle_and_ind_list, rows=legend_counter - 1, cols=1)
    fig.update_xaxes(row=1, col=1, rangeslider_visible=False)
    
    for indicator_dict_value in indicator_dict.values():
        indicator_list = []
        for ind_key, ind_value in indicator_dict_value.items():
            if "values" in ind_key:
                temp_ind_vals = ind_value.values.flatten()
                indicator_list.append(
                    go.Scatter(
                        x=index_prices,
                        y=temp_ind_vals,
                        mode="lines",
                    )
                )
            elif "entries" in ind_key:
                temp_ind_entries = np.where(
                    ind_value.values.flatten(), temp_ind_vals, np.nan
                ).flatten()
                indicator_list.append(
                    go.Scatter(
                        x=index_prices,
                        y=temp_ind_entries,
                        mode="markers",
                    )
                )
        fig.add_traces(data=indicator_list, rows=legend_counter, cols=1)
        legend_counter += 1

    fig.update_layout(height=layout_height)
    return fig.show()

In [4]:
def testing_strat_dashboard(
    indicator_dict: dict,
    prices,
    order_records,
):
    amount_of_subplots = 0

    for keys in indicator_dict.keys():
        if "indicator" in keys:
            amount_of_subplots += 1

    layout_height = 500 + (250 * amount_of_subplots)
    candle_chart_height_pct = [500 / layout_height]

    if amount_of_subplots > 0:
        subchart_heights_pct = np.array(
            [((layout_height - 500) / layout_height) / amount_of_subplots]
            * amount_of_subplots
        ).tolist()
        row_heights = candle_chart_height_pct + subchart_heights_pct
        fig = make_subplots(
            rows=amount_of_subplots + 1,
            cols=1,
            shared_xaxes=True,
            vertical_spacing=0.02,
            row_heights=row_heights,
        )
    else:
        fig = make_subplots()

    index_prices = prices.index.to_list()
    open_prices = prices.open.values
    high_prices = prices.high.values
    low_prices = prices.low.values
    close_prices = prices.close.values

    # candle chart trace
    fig.add_traces(
        data=get_candle_trace_data(
            index_prices=index_prices,
            open_prices=open_prices,
            high_prices=high_prices,
            low_prices=low_prices,
            close_prices=close_prices,
            order_records=order_records,
            indicator_dict=indicator_dict,
        ),
        rows=1,
        cols=1,
    )
    del indicator_dict["candle_chart"]
    row_count = 2
    for indicator_dict_value in indicator_dict.values():
        trace_data_list = []
        temp_ind_vals = np.array([0], dtype=object)
        for ind_key, ind_value in indicator_dict_value.items():
            append_to_trace_data_list(
                trace_data_list=trace_data_list,
                index_prices=index_prices,
                dict_key=ind_key,
                dict_value=ind_value,
                temp_ind_vals=temp_ind_vals,
            )
        fig.add_traces(
            data=trace_data_list,
            rows=row_count,
            cols=1,
        )
        row_count += 1
    fig.update_xaxes(row=1, col=1, rangeslider_visible=False)
    fig.update_yaxes(row=1, col=1, tickprefix="$")
    fig.update_layout(
        height=1000,
        legend_tracegroupgap=500,
        paper_bgcolor="#0b0b18",
        plot_bgcolor="#0b0b18",
    )
    return fig.show()

In [5]:
indicator_dict = {
    "candle_chart": {
        "values1": ema_ind[600],
        "values2": ema_ind[200],
    },
    "indicator1": {
        "values1": rsi_ind[15],
        "entries1": rsi_eval[15][40],
    },
    # "indicator2": {
    #     "values1": rsi_ind[15],
    #     "entries1": rsi_eval[15][40],
    # },
    # "indicator3": {
    #     "values1": rsi_ind[15],
    #     "entries1": rsi_eval[15][40],
    # },
    # "indicator4": {
    #     "values1": rsi_ind[15],
    #     "entries1": rsi_eval[15][40],
    # },
    # "indicator5": {
    #     "values1": rsi_ind[15],
    #     "entries1": rsi_eval[15][40],
    # },
}
testing_strat_dashboard(
    indicator_dict=indicator_dict,
    prices=prices,
    order_records=order_records,
)